In [14]:
# Stop warnings
# -------------
import warnings
warnings.filterwarnings("ignore")

# General imports
# ---------------
import sys
import numpy as np
import scipy.io
import glob
import datetime
import json

# MRI analysis imports
# --------------------
from prfpy.rf import *
from prfpy.timecourse import *
from prfpy.stimulus import PRFStimulus2D
from prfpy.model import Iso2DGaussianModel
from prfpy.fit import Iso2DGaussianFitter
import nibabel as nb

In [15]:
# Get inputs
# ----------
subject = 'sub-01'
preproc = 'fmriprep_dct_pca'
slice_nb = 7
regist_type = 'T1w'
opfn = ''
start_time = datetime.datetime.now()

# Define analysis parameters
with open('mri_analysis/settings.json') as f:
    json_s = f.read()
    analysis_info = json.loads(json_s)

# Define cluster/server specific parameters
base_dir = analysis_info['base_dir']
nb_procs = 32

# Get pmf sequence played
pmf_seq_num_all = analysis_info['pmf_seq_num']
pmf_seq_num = pmf_seq_num_all[int(subject[-2:])-1]

In [3]:
# Load data
data_file = "{base_dir}/pp_data/{sub}/func/{sub}_task-pMF_space-{reg}_{preproc}_avg.nii.gz".format(
                        base_dir = base_dir, sub = subject, reg = regist_type, preproc = preproc)
data_img = nb.load(data_file)
data = data_img.get_fdata()
data_var = np.var(data,axis=3)
mask = data_var!=0.0

slice_mask = mask[:,:,slice_nb].astype(bool)
num_vox = np.sum(slice_mask)
data_slice = data[:,:,slice_nb,:]
data_to_analyse = data_slice[slice_mask]

# determine voxel indices
y, x = np.meshgrid( np.arange(data.shape[1]),np.arange(data.shape[0]))
x_vox,y_vox = x[slice_mask],y[slice_mask]
vox_indices = [(xx,yy,slice_nb) for xx,yy in zip(x_vox,y_vox)]


In [17]:
visual_dm_file = scipy.io.loadmat("{base_dir}/pp_data/visual_dm/pMF_vd_{pmf_seq_num}.mat".format(base_dir=base_dir, pmf_seq_num=pmf_seq_num))
visual_dm = visual_dm_file['stim'].transpose([1,0,2])


stimulus = PRFStimulus2D(screen_width_cm = analysis_info['screen_width'],
                         screen_height_cm = analysis_info['screen_width'], # make it as width as saccades can go out of the pixel of the screen 
                         screen_distance_cm = analysis_info['screen_distance'],
                         design_matrix = visual_dm,
                         TR = analysis_info['TR'])

In [18]:
gauss_model = Iso2DGaussianModel(stimulus = stimulus)

grid_nr = analysis_info['grid_nr']
max_ecc_size = analysis_info['max_ecc_size']
sizes = max_ecc_size * np.linspace(0.25,1,grid_nr)**2
eccs = max_ecc_size * np.linspace(0.1,1,grid_nr)**2
polars = np.linspace(0, 2*np.pi, grid_nr)


In [19]:
print("Slice {slice_nb} containing {num_vox} brain mask voxels".format(slice_nb = slice_nb, num_vox = num_vox))

# grid fit
print("Grid fit")
gauss_fitter = Iso2DGaussianFitter(data = data_to_analyse, model = gauss_model, n_jobs = nb_procs)
gauss_fitter.grid_fit(ecc_grid = eccs, polar_grid = polars, size_grid = sizes, pos_prfs_only = True)

Slice 7 containing 144 brain mask voxels
Grid fit


In [20]:
# # iterative fit
# print("Iterative fit")
# gauss_fitter.iterative_fit(rsq_threshold = 0.0001, verbose = False)
# estimates_fit = gauss_fitter.iterative_search_params


In [21]:
print(dir(gauss_model))

['__class__', '__delattr__', '__dict__', '__dir__', '__doc__', '__eq__', '__format__', '__ge__', '__getattribute__', '__gt__', '__hash__', '__init__', '__init_subclass__', '__le__', '__lt__', '__module__', '__ne__', '__new__', '__reduce__', '__reduce_ex__', '__repr__', '__setattr__', '__sizeof__', '__str__', '__subclasshook__', '__weakref__', 'convolve_timecourse_hrf', 'create_drifts_and_noise', 'create_grid_predictions', 'create_hrf', 'create_rfs', 'eccs', 'filter_params', 'filter_predictions', 'filter_type', 'filtered_predictions', 'grid_rfs', 'hrf', 'normalize_RFs', 'polars', 'predictions', 'return_prediction', 'sizes', 'stimulus', 'stimulus_times_prfs', 'xs', 'ys']


In [22]:
import plotly.express as px
prf = gauss_model.grid_rfs[920,:,:]

fig = px.imshow(prf)
fig.show()

In [23]:
y = gauss_model.predictions[920,:]
fig = px.line(y=y)
fig.show()

In [24]:
# plot pmf seq 0 visual design
import plotly.express as px
visual_dm_file = scipy.io.loadmat("{base_dir}/pp_data/visual_dm/pMF_vd_seq1.mat".format(base_dir=base_dir))
visual_dm = visual_dm_file['stim'].transpose([2,1,0])
# fig = px.imshow(visual_dm, animation_frame=0,color_continuous_scale='gray',zmin=0,zmax=255)
# fig.show()

In [50]:
# plot pmf seq 0 visual design
import plotly.express as px
visual_dm_file = scipy.io.loadmat("{base_dir}/pp_data/visual_dm/pMF_vd_seq18.mat".format(base_dir=base_dir))
visual_dm = visual_dm_file['stim'].transpose([2,1,0])
fig = px.imshow(visual_dm, animation_frame=0,color_continuous_scale='gray',zmin=0,zmax=255)
fig.show()

In [6]:
fig = px.imshow(visual_dm, animation_frame=0,color_continuous_scale='gray',zmin=0,zmax=255)
fig.show()